In [7]:
import requests
import sqlite3
import threading
import json
import pandas as pd

URL_open = "https://www.opencve.io/api/vendors/{}/cve?page={}"
auth = ('YingliDuan', 'ocveLXRdyl844')

header = {"Authorization": "token user:679c2955085b46e48155b84f4c878844",}
URL="https://services.nvd.nist.gov/rest/json/cves/2.0?cveId={}"
URL_keyword="https://services.nvd.nist.gov/rest/json/cves/2.0?keywordSearch={}"

PATH="data/WiGLE_Backup.db"
cve0="cve_basic"
cve1="cve_metrics_2"
cve2="cve_metrics_3"
cve3="cve_weaknesses"


response = requests.get(URL_keyword.format('CVE-2023-31199'), auth=auth)

if response.status_code == 200:
    # Success! Do something with the response data
    data = response.json()
    print(len(data))
    print(data)
else:
    # Error
    print(f"Request failed with status code {response.status_code}")


7
{'resultsPerPage': 1, 'startIndex': 0, 'totalResults': 1, 'format': 'NVD_CVE', 'version': '2.0', 'timestamp': '2023-05-26T18:20:24.263', 'vulnerabilities': [{'cve': {'id': 'CVE-2023-31199', 'sourceIdentifier': 'secure@intel.com', 'published': '2023-05-12T15:15:09.527', 'lastModified': '2023-05-24T15:46:27.170', 'vulnStatus': 'Analyzed', 'descriptions': [{'lang': 'en', 'value': 'Improper access control in the Intel(R) Solid State Drive Toolbox(TM) before version 3.4.5 may allow a privileged user to potentially enable escalation of privilege via local access.'}], 'metrics': {'cvssMetricV31': [{'source': 'nvd@nist.gov', 'type': 'Primary', 'cvssData': {'version': '3.1', 'vectorString': 'CVSS:3.1/AV:L/AC:L/PR:H/UI:N/S:U/C:H/I:H/A:H', 'attackVector': 'LOCAL', 'attackComplexity': 'LOW', 'privilegesRequired': 'HIGH', 'userInteraction': 'NONE', 'scope': 'UNCHANGED', 'confidentialityImpact': 'HIGH', 'integrityImpact': 'HIGH', 'availabilityImpact': 'HIGH', 'baseScore': 6.7, 'baseSeverity': 'MED

In [5]:
# https://nvd.nist.gov/developers/vulnerabilities
import requests

url=URL_open.format('intel',1)
response = requests.get(url, auth=auth)
print(response.json())

[{'id': 'CVE-2023-31199', 'summary': 'Improper access control in the Intel(R) Solid State Drive Toolbox(TM) before version 3.4.5 may allow a privileged user to potentially enable escalation of privilege via local access.', 'created_at': '2023-05-12T15:15:00Z', 'updated_at': '2023-05-24T15:46:00Z'}, {'id': 'CVE-2023-31197', 'summary': 'Uncontrolled search path in the Intel(R) Trace Analyzer and Collector before version 2020 update 3 may allow an authenticated user to potentially enable escalation of privilege via local access.', 'created_at': '2023-05-12T15:15:00Z', 'updated_at': '2023-05-24T15:42:00Z'}, {'id': 'CVE-2023-30768', 'summary': 'Improper access control in the Intel(R) Server Board S2600WTT belonging to the Intel(R) Server Board S2600WT Family with the BIOS version 0016 may allow a privileged user to potentially enable escalation of privilege via local access.', 'created_at': '2023-05-12T15:15:00Z', 'updated_at': '2023-05-24T15:30:00Z'}, {'id': 'CVE-2023-30763', 'summary': 'H

In [17]:
import time
def insertDB(theme,results,keywords):
    con = sqlite3.connect(PATH)
    c = con.cursor()
    print("----insert vulnerabilities into database----")
    print("******** {},{}********".format(theme,keywords))
    print(results)
    #data_es=results['vulnerabilities']
    data_es=results
    #print(data_es)
    i_b = 0
    i_m=0
    i_w=0
    for data in data_es:
        for des in data.get('cve').get("descriptions"):
            i_b+=1
            #print(des)
            c.execute('''INSERT OR IGNORE INTO cve_basic (id, published, lastModified, vulnStatus, description_value,keywords)
                 VALUES (?, ?, ?, ?, ?, ?)''',
                 (data.get('cve').get('id'),
                  data.get('cve').get('published'),
                  data.get('cve').get('lastModified'),
                  data.get('cve').get('vulnStatus'),
                  des.get('value'),
                  keywords,
                 ))
        
        cvsses=list(data.get('cve').get("metrics").keys())
        if cvsses is not None:
            for cvss in cvsses:
                items = data.get('cve').get('metrics').get(cvss)
                if "cvssMetricV2" in cvss:
                    for item in items:
                        i_m+=1
                        c.execute('''INSERT OR IGNORE INTO cve_metrics_2 (id, cvss_type,type, cvssVersion, vectorString, accessVector, accessComplexity,
                             authentication, confidentialityImpact, integrityImpact, availabilityImpact, baseScore, baseSeverity,
                             exploitabilityScore, impactScore, acInsufInfo, obtainAllPrivilege, obtainUserPrivilege, obtainOtherPrivilege,
                             userInteractionRequired)
                             VALUES (?, ?, ?, ?,  ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?,?,?)''',
                             (data.get('cve').get('id'),
                              cvss,
                              item.get('type'),
                              item.get('cvssData').get('version'),
                              item.get('cvssData').get('vectorString'),
                              item.get('cvssData').get('accessVector'),
                              item.get('cvssData').get('accessComplexity'),
                              item.get('cvssData').get('authentication'),
                              item.get('cvssData').get('confidentialityImpact'),
                              item.get('cvssData').get('integrityImpact'),
                              item.get('cvssData').get('availabilityImpact'),
                              item.get('cvssData').get('baseScore'),
                              item.get('baseSeverity'),
                              item.get('exploitabilityScore'),
                              item.get('impactScore'),
                              item.get('acInsufInfo'),
                              item.get('obtainAllPrivilege'),
                              item.get('obtainUserPrivilege'),
                              item.get('obtainOtherPrivilege'),
                              item.get('userInteractionRequired')))
                if "cvssMetricV3" in cvss:
                    for item in items:
                        i_m+=1
                        c.execute('''INSERT OR IGNORE INTO cve_metrics_3 (id, cvss_type, type, cvssVersion, vectorString, attackVector, attackComplexity,
                                 privilegesRequired, userInteraction, scope, confidentialityImpact, integrityImpact, availabilityImpact, baseScore, baseSeverity,
                                 exploitabilityScore, impactScore)
                                 VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)''',
                                 (data.get('cve').get('id'),
                                  cvss,
                                  item.get('type'),
                                  item.get('cvssData').get('version'),
                                  item.get('cvssData').get('vectorString'),
                                  item.get('cvssData').get('attackVector'),
                                  item.get('cvssData').get('attackComplexity'),
                                  item.get('cvssData').get('privilegesRequired'),
                                  item.get('cvssData').get('userInteraction'),
                                  item.get('cvssData').get('scope'),
                                  item.get('cvssData').get('confidentialityImpact'),
                                  item.get('cvssData').get('integrityImpact'),
                                  item.get('cvssData').get('availabilityImpact'),
                                  item.get('cvssData').get('baseScore'),
                                  item.get('cvssData').get('baseSeverity'),
                                  item.get('exploitabilityScore'),
                                  item.get('impactScore')))
        weaknesses=data.get('cve').get('weaknesses')
        if weaknesses is not None:
            for weak in weaknesses:
                for value in weak['description']:
                    i_w+=1
                    #(data.get('cve').get('id'),weak.get('type'),value)
                    #print(data.get('cve').get('id'),weak.get('type'),value)

                    c.execute('''INSERT OR IGNORE INTO cve_weaknesses (id,type,description_value) VALUES(?,?,?)''',
                            (data.get('cve').get('id'),weak.get('type'),value.get("value")))
    
    con.commit()
    con.close()
    print("cve_basic:", i_b)
    print("cve_metrics:", i_m)
    print("cve_weaknesses:", i_w)
    print("---- DONE {}----".format(keywords))

def collect_load_CVE(cve_dict,title,url):
    con = sqlite3.connect(PATH)
    cur = con.cursor()
    sql="select * from {} ".format(cve0)
    cve_rt=pd.read_sql_query(sql, con)
    con.close()
    
    results_types=dict.fromkeys(cve_dict)
    flag=False
    
    for rt in results_types:
        cves=cve_dict[rt]
        cves_rt=[]
        for cve in cves:
            
#             if rt=='acer':
#                 flag=True
            flag=True        
            if cve in cve_rt['id'].values:
                flag=False
            if flag==True:
                url_n = url.format(cve)
                
                print(url_n)
                response = requests.get(url_n)
                #print(response.json())
                if response.status_code==200:
                    cves_rt.append(response.json()['vulnerabilities'][0])
                print(response.status_code)
                time.sleep(6)
        print("UPLODING")
        insertDB(title,cves_rt,rt)

# A ratelimit of 1000 requests per hour and per user is applied on OpenCVE.io.
cves={}
def collect_cve_id(vendors):
    request_times=0
    
    con = sqlite3.connect(PATH)
    cur = con.cursor()
    vendor_flag=False
    for vendor in vendors:
        print(vendor,"-")
        page=1
        flag=True
        
        
        if vendor=='telrad':
            vendor_flag=True
        if vendor_flag==False:
            continue
        
        sql="select * from {} where keywords='{}'".format(cve0,vendor)
        rt=cur.execute(sql).fetchall()
        print(vendor,len(rt))
        if len(rt)!=0:
            print("vendor {} found".format(vendor))
            continue        
        
        vendor_data=[]
        while flag:
            time.sleep(2)
            if flag==True:
                url=URL_open.format(vendor,page)
                print(url)
                response = requests.get(url, auth=auth)
                print(response.status_code)
                page+=1
                if response.status_code == 200:
                    # Success! Do something with the response data
                    data = response.json()
                    vendor_data=vendor_data+data
                    if len(data)<20:
                        flag=False
                        
                    print("length of this response:",len(data))
                else:
                    flag=False
                    print(f"Request failed with status code {response.status_code}")
                if response.status_code==429:
                    cves[vendor]=[ids['id'] for ids in vendor_data]
                    print("To much data in this hour")
                    con.close()
                    return cves
        cves[vendor]=[ids['id'] for ids in vendor_data]
    con.close()
    return cves

ULW_P=["EUROPE","BEIJING","SHENZHEN","AMERICA","SICHUAN","HUI","ZHOU","Hong","KONG","SHANGHAI","ASIA","CH","USA","BELGIUM",
       "ZHUHAI","GUANGZHOU"]# useless word-place
ULW_S=["COMPUTER","SYSTEMS","CO","LTD","LIMITED","CORPORATION","CORP","COMMUNCATIONS","COMMUNICATION","COMMUNICATIONS","ELECTRONIC","ELECTRONICS",
       "NETWORK","INC","LLC","COMPANY","INTERNATIONAL","WIRELESS","DATA","MEDICAL","AG","Electric","NETWORKING","ELECTRIC",
       "SRO","BV","SYS","INDUSTRIALS","INDUSTRIAL","DEVICE","DEVICES","COMM","TECHNOLOGY","TECHNOLOGIES","TECH","COLTD","A/S","DELIVERY","NV",
       "NETWORKS","APPLICATIONS","OF","APS","GROUP","IND","DEVELOPMENT","AS","AB","OY","IOT","INNOTEK","GMBH","AUDIOVISUELLES",
       "MARKETING","UND","COMPUTERSYSTEME","MACHINE","ELECTRO","MECHANICS","MOBILE","SOFTWARE","DIGITAL","TECHLTD","INFORMATION",
      "AUTOMOTIVE","CORPORATE","ENTERPRISE","LABORATORY","LABORATORIES"] # useless word-suffix
def clean_name(vendors,cur):
    vens=[]
    vendors=list(vendors)
    
    for vendor in vendors:
        rt=vendor[0].replace(",","").replace(".","").replace("\n","").replace("，","").replace("'","")
        rt_s=rt.split(" ")
        if rt_s[0]=="Harman/Becker":
            name=["Harman"]
        elif rt_s[0]=="Nokia":
            name=["Nokia"]
        else:
            name=[r for r in rt_s if r.upper() not in ULW_P and r.upper() not in ULW_S and "(" not in r and ")" not in r]
        #print(name)
        if len(name)!=0:
            sql="select * from {} where keywords='{}'".format(cve0,name[0].lower())
            #if len(cur.execute(sql).fetchall())==0 and name[0]!='':
            if name[0]!='':
                vens.append(name[0].lower())
    return vens

# Vendors of WiFi

In [14]:
con = sqlite3.connect(PATH)
cur = con.cursor()

sql="""SELECT DISTINCT vendor.OrganizationName
        FROM vendor
        JOIN (
            SELECT bssid 
            FROM network 
            WHERE type = 'W'
            UNION ALL 
            SELECT netid 
            FROM wigle_wifi
        ) AS network_wifi ON network_wifi.bssid = vendor.mac
        GROUP BY vendor.OrganizationName
        """
rts=cur.execute(sql).fetchall()
print("******Results of WiFi*******\n",len(rts),rts)
rts_wf=list(set(clean_name(rts,cur)))
print("********CLEANED NAME*********\n",len(rts_wf),rts_wf)

sql="""select distinct keywords
        from cve_basic
"""
rts=cur.execute(sql).fetchall()
print("keywords in possesed vulunerabilities:",len(rts))
rts_wf_1=[]
for r in rts_wf:
    if r in rts:
        continue
    rts_wf_1.append(r)
print("********FILTER*********\n",len(rts_wf_1),rts_wf_1)


con.close()


******Results of WiFi*******
 364 [('3COM\n',), ('3COM EUROPE LTD\n',), ('3D Display Technologies Co., Ltd.\n',), ('70mai Co.,Ltd.\n',), ('7INOVA TECHNOLOGY LIMITED\n',), ('8Devices\n',), ('@pos.com\n',), ('ACCTON TECHNOLOGY CORP.\n',), ('ACTIA\n',), ('AIRTAME ApS\n',), ('ALPSALPINE CO,.LTD\n',), ('AMIT, Inc.\n',), ('AMPAK Technology, Inc.\n',), ('APPLIED MICROSYSTEMS CORP.\n',), ('ARRIS Group, Inc.\n',), ('ASANTE TECHNOLOGIES\n',), ('ASKEY COMPUTER CORP\n',), ('ASUSTek COMPUTER INC.\n',), ('AVM Audiovisuelles Marketing und Computersysteme GmbH\n',), ('AVM GmbH\n',), ('AboCom\n',), ('Accelerated Concepts, Inc\n',), ('Aceex Corporation\n',), ('Acer Incorporated\n',), ('Actia Automotive\n',), ('Actions Microelectronics Co., Ltd\n',), ('Agere Systems\n',), ('Air Link Technology\n',), ('AirTies Wireless Networks\n',), ('Allied Data Technologies\n',), ('AltoBeam (China) Inc.\n',), ('Ambit Microsystems Corporation\n',), ('Apple, Inc.\n',), ('Arlo Technology\n',), ('Aruba, a Hewlett Packard E

In [19]:
cveIDs=collect_cve_id(rts_wf_1)
print(len(cveIDs),cveIDs)

ring -
voyetra -
motorola -
cybertan -
hon -
mercury -
icotera -
inteno -
abocom -
gree -
trendnet -
netgear -
smartbridges -
z-com -
clipcomm -
hong -
zte -
sendtek -
sophos -
edup -
hp -
ericsson -
buffaloinc -
uniwill -
netspect -
xavi -
seongji -
reecam -
lg -
guangzhou shiyuan electronic technology company limited -
70mai -
puretek -
netcore -
colubris -
unidata -
d-link -
inpro -
utstarcom -
yunlink -
mo -
hangzhou -
winstars -
azurewave -
cameo -
sonicwall -
zhejiang -
qcom -
routerboardcom -
quectel -
versa -
mist -
cisco -
xiaoyi -
technicolor -
otc -
accton -
d&m -
ford -
nexsi -
runtop -
microchip -
hongkong -
billion -
7inova -
nexcom -
nextcomm -
open -
asante -
chongqing -
nvidia -
raspberry -
haier -
mercusys -
hunan -
bmw -
compal -
fn-link -
intel -
telrad -
telrad 0
https://www.opencve.io/api/vendors/telrad/cve?page=1
404
Request failed with status code 404
magneti -
magneti 0
https://www.opencve.io/api/vendors/magneti/cve?page=1
404
Request failed with status code 40

https://www.opencve.io/api/vendors/partron/cve?page=1
404
Request failed with status code 404
apple -
apple 20
vendor apple found
atheros -
atheros 6
vendor atheros found
cellvision -
cellvision 0
https://www.opencve.io/api/vendors/cellvision/cve?page=1
404
Request failed with status code 404
new -
new 0
https://www.opencve.io/api/vendors/new/cve?page=1
404
Request failed with status code 404
sifrom -
sifrom 0
https://www.opencve.io/api/vendors/sifrom/cve?page=1
404
Request failed with status code 404
devolo -
devolo 0
https://www.opencve.io/api/vendors/devolo/cve?page=1
404
Request failed with status code 404
nokia -
nokia 35
vendor nokia found
trolink -
trolink 0
https://www.opencve.io/api/vendors/trolink/cve?page=1
404
Request failed with status code 404
gemicom -
gemicom 0
https://www.opencve.io/api/vendors/gemicom/cve?page=1
404
Request failed with status code 404
xerox -
xerox 39
vendor xerox found
timeplex -
timeplex 0
https://www.opencve.io/api/vendors/timeplex/cve?page=1
404
R

404
Request failed with status code 404
rf-link -
rf-link 0
https://www.opencve.io/api/vendors/rf-link/cve?page=1
404
Request failed with status code 404
allied -
allied 0
https://www.opencve.io/api/vendors/allied/cve?page=1
404
Request failed with status code 404
realtek -
realtek 37
vendor realtek found
robustel -
robustel 40
vendor robustel found
winmate -
winmate 0
https://www.opencve.io/api/vendors/winmate/cve?page=1
404
Request failed with status code 404
air -
air 0
https://www.opencve.io/api/vendors/air/cve?page=1
404
Request failed with status code 404
siliconware -
siliconware 0
https://www.opencve.io/api/vendors/siliconware/cve?page=1
404
Request failed with status code 404
watchguard -
watchguard 40
vendor watchguard found
tct -
tct 0
https://www.opencve.io/api/vendors/tct/cve?page=1
404
Request failed with status code 404
pro-nets -
pro-nets 0
https://www.opencve.io/api/vendors/pro-nets/cve?page=1
404
Request failed with status code 404
actia -
actia 0
https://www.opencve.

https://www.opencve.io/api/vendors/qnap/cve?page=5
200
length of this response: 20
https://www.opencve.io/api/vendors/qnap/cve?page=6
200
length of this response: 20
https://www.opencve.io/api/vendors/qnap/cve?page=7
200
length of this response: 20
https://www.opencve.io/api/vendors/qnap/cve?page=8
200
length of this response: 20
https://www.opencve.io/api/vendors/qnap/cve?page=9
200
length of this response: 20
https://www.opencve.io/api/vendors/qnap/cve?page=10
200
length of this response: 14
labtam -
labtam 0
https://www.opencve.io/api/vendors/labtam/cve?page=1
404
Request failed with status code 404
sony -
sony 39
vendor sony found
lesswire -
lesswire 0
https://www.opencve.io/api/vendors/lesswire/cve?page=1
404
Request failed with status code 404
sichuan ai-link technology co ltd -
sichuan ai-link technology co ltd 0
https://www.opencve.io/api/vendors/sichuan ai-link technology co ltd/cve?page=1
404
Request failed with status code 404
enterasys -
enterasys 14
vendor enterasys found


In [20]:
collect_load_CVE(cveIDs,"WiFi Vendors",url=URL)

UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,telrad********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE telrad----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,magneti********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE magneti----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,freecom********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE freecom----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,inhand********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE inhand----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,smart********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE smart----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-8087
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-7249
200
https://services.nvd.nist.gov/rest/json/cves/2.

cve_basic: 6
cve_metrics: 5
cve_weaknesses: 3
---- DONE smc----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,creatix********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE creatix----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,actions********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE actions----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,yaojin********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE yaojin----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,balboa********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE balboa----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,quantenna********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE quantenna----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,makino********
[]
cve_basic: 0
cve_metrics: 0

cve_basic: 9
cve_metrics: 9
cve_weaknesses: 7
---- DONE zebra----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,china********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE china----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,freebox********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE freebox----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,baudtec********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE baudtec----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,chicony********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE chicony----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-27152
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-11314
200
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,roku********
[{'cve': {'id': 'CVE-2022-27152', 'sourceIdentifi

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2007-4753
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2007-4553
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2006-0946
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2005-0494
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2004-0641
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2003-1085
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2014-4716
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2006-0947
200
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,thomson********
[{'cve': {'id': 'CVE-2007-6003', 'sourceIdentifier': 'cve@mitre.org', 'published': '2007-11-15T22:46:00.000', 'lastModified': '2017-07-29T01:33:59.193', 'vulnStatus': 'Modified', 'descriptions': [{'lang': 'en', 'value': 'Cross-site scripting (XSS) vulnerability in cgi/b/ic/connect in the Thomson SpeedTouch 716 with fir

cve_basic: 13
cve_metrics: 9
cve_weaknesses: 9
---- DONE thomson----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,ligowave********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE ligowave----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,partron********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE partron----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,cellvision********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE cellvision----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,new********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE new----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,sifrom********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE sifrom----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,devolo********
[]
cve_basic: 0
cve_metrics

...

cve_basic: 467
cve_metrics: 578
cve_weaknesses: 394
---- DONE synology----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,eero********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE eero----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,gainspan********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE gainspan----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,sureman********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE sureman----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,bromax********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE bromax----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,xircom********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE xircom----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2014-3889
200
https://services.nvd.nist.gov/rest/json/cves/

cve_basic: 7
cve_metrics: 10
cve_weaknesses: 5
---- DONE miele----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,pepwave********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE pepwave----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,global********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE global----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,wistron********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE wistron----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,silicon********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE silicon----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,libratone********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE libratone----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,u-blox********
[]
cve_basic: 0
cve_metri

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-27597
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-23355
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-7201
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-27596
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-7185
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-7184
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-19956
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-19955
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-19954
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-19951
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-19950
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-2506
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-28798
200
https://services.nvd.nist.gov/rest/jso

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-19947
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-19948
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-19946
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-7876
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-0730
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-0729
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-2500
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-7193
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2013-6277
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-0721
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-0719
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-7183
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-0728
200
https://services.nvd.nist.gov/rest/json/cves

cve_basic: 384
cve_metrics: 458
cve_weaknesses: 342
---- DONE qnap----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,labtam********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE labtam----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,lesswire********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE lesswire----
UPLODING
----insert vulnerabilities into database----
******** WiFi Vendors,sichuan ai-link technology co ltd********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE sichuan ai-link technology co ltd----


In [29]:
cveIDs_1=collect_cve_id(rts)
print(len(cveIDs_1),cveIDs_1)
#

ford -
puretek -
dovado -
8devices -
3d -
barrot -
netspect -
hmd -
lifi -
inpro -
azurewave -
pittasoft -
billion -
makino -
shirui -
equiptrans -
hcl -
alpsalpine -
sena -
sureman -
sercomm -
prime -
sendtek -
freebox -
airtame -
espressif -
fairphone -
ibm -
intel -
intel 1805
200 https://www.opencve.io/api/vendors/intel/cve?page=51
length of this response: 20
200 https://www.opencve.io/api/vendors/intel/cve?page=52
length of this response: 20
200 https://www.opencve.io/api/vendors/intel/cve?page=53
length of this response: 20
200 https://www.opencve.io/api/vendors/intel/cve?page=54
length of this response: 20
200 https://www.opencve.io/api/vendors/intel/cve?page=55
length of this response: 20
200 https://www.opencve.io/api/vendors/intel/cve?page=56
length of this response: 20
200 https://www.opencve.io/api/vendors/intel/cve?page=57
length of this response: 20
200 https://www.opencve.io/api/vendors/intel/cve?page=58
length of this response: 20
200 https://www.opencve.io/api/vendors/

In [30]:
collect_load_CVE(cveIDs_1,"WiFi Vendors",url=URL)

https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12223
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12220
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12218
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12217
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12210
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12209
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12205
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12204
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12203
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12202
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12200
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12177
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12176
200
https://services.nvd.nist.gov/rest/jso

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-3699
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12169
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-3621
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-3650
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12149
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12150
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-3686
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-12151
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2008-3635
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2010-3268
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2006-2316
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2006-6385
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2008-3900
200
https://services.nvd.nist.gov/rest/json/cve

# Ciphers of WiFi
> ---------cipher-----------
  
    {'CCMP': 23470, 'TKIP+CCMP': 770, 'CCMP+TKIP': 1211, 'TKIP': 117, 'None+CCMP': 8}

In [ ]:
ciphers={'ciphers':['CCMP','TKIP','TKIP CCMP','CCMP TKIP']}
collect_load_CVE(cveIDs,"WiFi Vendors",url=URL_keyword)

# Key management
> {'EAP/SHA1': 3644, 'PSK': 21131, 'PSK+SAE': 176, 'EAP/SHA1+FT/EAP': 298, 'PSK+FT/PSK': 254, 
   'SAE': 18, 'EAP/SHA1+?': 44, 'PSK+PSK': 9, 'SHA256': 8, 'EAP/SHA1+EAP/SHA256': 6, 'SHA256+SAE': 1}

- it is nonesense to do this because cannot find exactly result

# Vendors of BT

In [4]:
con = sqlite3.connect(PATH)
cur = con.cursor()
sql="""SELECT DISTINCT vendor.OrganizationName
        FROM vendor
        JOIN (
            SELECT bssid as netid
            FROM network 
            WHERE type = 'B' or type = 'E'
            UNION ALL 
            SELECT netid
            FROM wigle_blue
        ) AS network_blue
        WHERE network_blue.netid = vendor.mac
        GROUP BY vendor.OrganizationName
        """
rts_BT=cur.execute(sql).fetchall()
print("******Results of BT*******\n",len(rts_BT),rts_BT)
rts_BT=list(set(clean_name(rts_BT,cur)))
print("********CLEANED NAME*********\n",len(rts_BT),rts_BT)

sql="""select distinct keywords
        from cve_basic
"""
rts=cur.execute(sql).fetchall()
print("keywords in possesed vulunerabilities:",len(rts))
rts_BT_1=[]
for r in rts_BT:
    if r in rts:
        continue
    rts_BT_1.append(r)
print("********FILTER*********\n",len(rts_BT_1),rts_BT_1)

con.close()


******Results of BT*******
 2406 [(' BST GmbH\n',), (' INGENICO TERMINALS SAS\n',), (' LongSung Technology (Shanghai) Co.,Ltd.   \n',), (' Vanderlande APC inc.\n',), (' Wingtech Group (HongKong）Limited\n',), ('10NET COMMUNICATIONS/DCA\n',), ('1394 Trade Association\n',), ('1MORE\n',), ('2Wire Inc\n',), ('360 Fly Inc.\n',), ('3COM\n',), ('3COM EUROPE LTD\n',), ('3CX\n',), ('3Com Ltd\n',), ('3D Systems Massachusetts\n',), ('3H TECHNOLOGY\n',), ('3M Germany\n',), ('4IPNET, INC.\n',), ('690885 Ontario Inc.\n',), ('70mai Co.,Ltd.\n',), ('77 Elektronika Kft.\n',), ('8BITDO TECHNOLOGY HK LIMITED\n',), ('8D Technologies\n',), ('@pos.com\n',), ('A.I. ANTITACCHEGGIO ITALIA SRL\n',), ('A2 CORPORATION\n',), ('ABB Inc./Tropos\n',), ('ABB Inc/Totalflow\n',), ('ACC GmbH\n',), ('ACCORD SYSTEMS, INC.\n',), ('ACKFIN NETWORKS\n',), ('ACTi Corporation\n',), ('ACX GmbH\n',), ('ADAPTIVE SYSTEMS, INC.\n',), ('ADB Broadband Italia\n',), ('ADEUNIS RF\n',), ('ADLINK TECHNOLOGY, INC.\n',), ('ADS GmbH\n',), ('ADS

keywords in possesed vulunerabilities: 236
********FILTER*********
 2121 ['integrated', 'saxa', 'prolon', 'southwest', 'aewin', 'amoi', 'realand', 'nanchang', 'novatium', 'aten', 'mercury', 'alfred', 'vsk', 'e-generis', 'avilinks', 'packard', 'synectics', 'sabioso', 'vizimax', 'cosworth', 'proliphix', 's-information', 'iptrade', 'starkey', 'nsm', 'wepio', 'camtronics', 'ktnf', 'shc', 'tattile', 'tatsuta', 'jing', 'britestream', 'paradox', 'emergent', 'ericsson', 'ctek', 'storcase', 'am', 'exo', 'venergycoltd', 'keico', 'sielox', 'torian', 'ingram', 'nexcomm', 'xavi', 'flash', 'imlogix', 'hazemeyer', 'huber', 'centillion', 'veea', 'cranite', 'seabridge', 'torch', 'bicc', 'goldstar', 'd-link', 'packet', 'presence', '&', 'cztic', 'modnnet', 'phonak', 'yves', 'innovations', 'zhiyuan', 'processing', 'kanda', 'shenztech', 'starvedia', 'technodrive', 'smartvue', 'voxtech', 'metro', 'ajoho', 'eukrea', 'acromag', 'gsi', 'loytec', 'digivoice', 'allis', 'metalligence', 'mobytel', 'nitgen', 'marco

In [5]:
cveIDs_BT=collect_cve_id(rts_BT_1)

integrated -
saxa -
prolon -
southwest -
aewin -
amoi -
realand -
nanchang -
novatium -
aten -
mercury -
alfred -
vsk -
e-generis -
avilinks -
packard -
synectics -
sabioso -
vizimax -
cosworth -
proliphix -
s-information -
iptrade -
starkey -
nsm -
wepio -
camtronics -
ktnf -
shc -
tattile -
tatsuta -
jing -
britestream -
paradox -
emergent -
ericsson -
ctek -
storcase -
am -
exo -
venergycoltd -
keico -
sielox -
torian -
ingram -
nexcomm -
xavi -
flash -
imlogix -
hazemeyer -
huber -
centillion -
veea -
cranite -
seabridge -
torch -
bicc -
goldstar -
d-link -
packet -
presence -
& -
cztic -
modnnet -
phonak -
yves -
innovations -
zhiyuan -
processing -
kanda -
shenztech -
starvedia -
technodrive -
smartvue -
voxtech -
metro -
ajoho -
eukrea -
acromag -
gsi -
loytec -
digivoice -
allis -
metalligence -
mobytel -
nitgen -
marconi -
cyfrowy -
team-r -
intervoice-brite -
clearwire -
koga -
barun -
merging -
mist -
fonsys -
gamesa -
cisco -
hand -
proteon -
respironics -
encanto -
gvn -
e

creative -
andritz -
aiconn -
actions -
lenbrook -
xtel -
qpsx -
lions -
ibm -
ato -
starguide -
seeed -
kyuden -
mobiwire -
freebox -
clarion -
sonova -
netac -
hill-rom -
zf -
metacomp -
sande -
icp -
designers -
vocollect -
bellmann -
nero -
taicang -
soyal -
union -
color -
omnitronix -
nuvyyo -
entridia -
lpl -
powerwallz -
toshiba -
metz-werke -
waters -
linxtek -
isys -
helmholtz -
synchronous -
lasercraft -
mondial -
honesty -
uhd-elektronik -
cosine -
nact -
elexol -
eri -
xian -
nbs -
zhs -
pomdevices -
gw -
dibosscoltd -
legrand -
bury -
earda -
juin -
hamp -
shinwa -
airocon -
variscite -
microscan -
2wire -
huawei -
home -
aruba -
mimaki -
alacritech -
canoga -
sagemcom -
crete -
nothing -
spe -
proteus -
satec -
miljovakt -
rtx -
xiaomi -
eazix -
mintera -
iridium -
moog -
jinwoo -
oa -
em -
meerecompany -
intelligent -
aonvision -
liecthi -
cochlear -
bowers -
powerhouse -
polypix -
longconn -
topwise -
wintech -
holy -
prentke -
tyco -
atheros -
rittal-werk -
cellvision

https://www.opencve.io/api/vendors/legic/cve?page=1
404
Request failed with status code 404
funkwerk -
funkwerk 0
https://www.opencve.io/api/vendors/funkwerk/cve?page=1
200
length of this response: 2
apple -
apple 20
vendor apple found
japan -
japan 0
https://www.opencve.io/api/vendors/japan/cve?page=1
404
Request failed with status code 404
leipold+cogmbh -
leipold+cogmbh 0
https://www.opencve.io/api/vendors/leipold+cogmbh/cve?page=1
404
Request failed with status code 404
concur -
concur 0
https://www.opencve.io/api/vendors/concur/cve?page=1
404
Request failed with status code 404
sifrom -
sifrom 0
https://www.opencve.io/api/vendors/sifrom/cve?page=1
404
Request failed with status code 404
suzuken -
suzuken 0
https://www.opencve.io/api/vendors/suzuken/cve?page=1
404
Request failed with status code 404
teledata -
teledata 0
https://www.opencve.io/api/vendors/teledata/cve?page=1
404
Request failed with status code 404
ohsung -
ohsung 0
https://www.opencve.io/api/vendors/ohsung/cve?page

404
Request failed with status code 404
chiaro -
chiaro 0
https://www.opencve.io/api/vendors/chiaro/cve?page=1
404
Request failed with status code 404
tozo -
tozo 0
https://www.opencve.io/api/vendors/tozo/cve?page=1
404
Request failed with status code 404
free -
free 14
vendor free found
hmd -
hmd 0
https://www.opencve.io/api/vendors/hmd/cve?page=1
404
Request failed with status code 404
elmegt -
elmegt 0
https://www.opencve.io/api/vendors/elmegt/cve?page=1
404
Request failed with status code 404
nanoptix -
nanoptix 0
https://www.opencve.io/api/vendors/nanoptix/cve?page=1
404
Request failed with status code 404
junqian -
junqian 0
https://www.opencve.io/api/vendors/junqian/cve?page=1
404
Request failed with status code 404
teldat -
teldat 0
https://www.opencve.io/api/vendors/teldat/cve?page=1
404
Request failed with status code 404
freescale -
freescale 0
https://www.opencve.io/api/vendors/freescale/cve?page=1
404
Request failed with status code 404
trunknet -
trunknet 0
https://www.op

404
Request failed with status code 404
orolia -
orolia 0
https://www.opencve.io/api/vendors/orolia/cve?page=1
404
Request failed with status code 404
west -
west 0
https://www.opencve.io/api/vendors/west/cve?page=1
404
Request failed with status code 404
eckelmann -
eckelmann 0
https://www.opencve.io/api/vendors/eckelmann/cve?page=1
404
Request failed with status code 404
ipaxiom -
ipaxiom 0
https://www.opencve.io/api/vendors/ipaxiom/cve?page=1
404
Request failed with status code 404
coosea -
coosea 0
https://www.opencve.io/api/vendors/coosea/cve?page=1
404
Request failed with status code 404
infineon -
infineon 6
vendor infineon found
avtec -
avtec 0
https://www.opencve.io/api/vendors/avtec/cve?page=1
404
Request failed with status code 404
kimball -
kimball 0
https://www.opencve.io/api/vendors/kimball/cve?page=1
404
Request failed with status code 404
saf -
saf 0
https://www.opencve.io/api/vendors/saf/cve?page=1
404
Request failed with status code 404
tbtech -
tbtech 0
https://www.o

404
Request failed with status code 404
zed-3 -
zed-3 0
https://www.opencve.io/api/vendors/zed-3/cve?page=1
200
length of this response: 2
sysmate -
sysmate 0
https://www.opencve.io/api/vendors/sysmate/cve?page=1
404
Request failed with status code 404
baidu -
baidu 30
vendor baidu found
keysight -
keysight 15
vendor keysight found
texas -
texas 0
https://www.opencve.io/api/vendors/texas/cve?page=1
404
Request failed with status code 404
cubix -
cubix 0
https://www.opencve.io/api/vendors/cubix/cve?page=1
404
Request failed with status code 404
harman -
harman 18
vendor harman found
sz -
sz 0
https://www.opencve.io/api/vendors/sz/cve?page=1
404
Request failed with status code 404
fresh -
fresh 0
https://www.opencve.io/api/vendors/fresh/cve?page=1
404
Request failed with status code 404
lesswire -
lesswire 0
https://www.opencve.io/api/vendors/lesswire/cve?page=1
404
Request failed with status code 404
jasco -
jasco 0
https://www.opencve.io/api/vendors/jasco/cve?page=1
200
length of this 

In [35]:
collect_load_CVE(cveIDs_BT,"BT Vendors",url=URL)

UPLODING
----insert vulnerabilities into database----
******** BT Vendors,avery********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE avery----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,watertek********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE watertek----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,azteq********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE azteq----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,bay********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE bay----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,dickens********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE dickens----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,systemhouse********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE systemhouse----
https://services.nvd.nist.gov/rest/json/

cve_basic: 12
cve_metrics: 10
cve_weaknesses: 6
---- DONE ntp----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,g-pro********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE g-pro----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,leading********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE leading----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,alloptic********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE alloptic----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,lattice********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE lattice----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,vxi********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE vxi----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,escalate********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-2790
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-2792
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-2793
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-2788
200
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,emerson********
[{'cve': {'id': 'CVE-2022-2791', 'sourceIdentifier': 'ics-cert@hq.dhs.gov', 'published': '2022-11-22T20:15:10.917', 'lastModified': '2022-11-26T03:32:31.460', 'vulnStatus': 'Analyzed', 'descriptions': [{'lang': 'en', 'value': "Emerson Electric's Proficy Machine Edition Version 9.00 and prior is vulnerable to CWE-434 Unrestricted Upload of File with Dangerous Type, and will upload any file written into the PLC logic folder to the connected PLC."}], 'metrics': {'cvssMetricV31': [{'source': 'nvd@nist.gov', 'type': 'Primary', 'cvssData': {'version': '3.1', 'vectorString': 'CVSS:3.1/AV:L/AC:L/PR:L/UI:N/S:U/C:H/I

cve_basic: 9
cve_metrics: 10
cve_weaknesses: 7
---- DONE emerson----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,telencomm********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE telencomm----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,general********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE general----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,kunshan********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE kunshan----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,kumahira********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE kumahira----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,t-mac********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE t-mac----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,lets********
[]
cve_basic: 0
cve_metrics: 0
cve_we

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-10616
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-0053
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2015-5361
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2009-1185
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2015-3209
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-22404
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-22405
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-22187
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-10617
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-22400
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-22399
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-22398
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-22397
200
https://services.nvd.nist.gov/rest/jso

...

cve_basic: 1400
cve_metrics: 1565
cve_weaknesses: 1110
---- DONE juniper----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-1967
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-1860
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-1399
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-38129
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-38130
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-1660
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-1661
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-35121
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-35122
200
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,keysight********
[{'cve': {'id': 'CVE-2023-1967', 'sourceIdentifier': 'ics-cert@hq.dhs.gov', 'published': '2023-04-27T22:15:09.187', 'lastModified': '2023-05-05T17:14:43.903', 'vulnStatus'

cve_basic: 15
cve_metrics: 18
cve_weaknesses: 11
---- DONE keysight----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,diebold********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE diebold----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,entrada********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE entrada----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,integrated********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE integrated----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,maquet********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE maquet----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,pharmasmart********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE pharmasmart----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,centillion********
[]
cve_basic: 0
cv

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-28613
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-1168
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-27196
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-0580
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-3192
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-1258
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-4126
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-26080
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-3573
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-22283
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-0228
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-1607
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-18996
200
https://services.nvd.nist.gov/rest/json/cv

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-10616
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-7931
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-9664
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-7920
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-7906
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-7916
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-16731
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-14025
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-7933
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-20720
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2008-2474
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2012-1801
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-15583
200
https://services.nvd.nist.gov/rest/json/cv

cve_basic: 221
cve_metrics: 287
cve_weaknesses: 217
---- DONE abb----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,cierma********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE cierma----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,nexcomm********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE nexcomm----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,uhd-elektronik********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE uhd-elektronik----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,serverengines********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE serverengines----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,metalligence********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE metalligence----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,dwnet********
[]


In [37]:
collect_load_CVE(cveIDs_BT,"BT Vendors",url=URL)

UPLODING
----insert vulnerabilities into database----
******** BT Vendors,fresh********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE fresh----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,ketron********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE ketron----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,resol********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE resol----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,ymc********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE ymc----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,utility********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE utility----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,nct********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE nct----
UPLODING
----insert vulnerabilities into database----
******

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-36631
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-31830
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-37271
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-22741
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-18145
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2018-0692
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2007-4105
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2008-7013
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2008-6444
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2009-2970
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-14744
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-2221
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-2219
200
https://services.nvd.nist.gov/rest/json/c

cve_basic: 30
cve_metrics: 24
cve_weaknesses: 16
---- DONE baidu----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-33505
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-8339
200
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,falco********
[{'cve': {'id': 'CVE-2021-33505', 'sourceIdentifier': 'cve@mitre.org', 'published': '2021-07-15T11:15:07.900', 'lastModified': '2021-07-28T14:04:51.713', 'vulnStatus': 'Analyzed', 'descriptions': [{'lang': 'en', 'value': 'A local malicious user can circumvent the Falco detection engine through 0.28.1 by running a program that alters arguments of system calls being executed. Issue is fixed in Falco versions >= 0.29.1.'}, {'lang': 'es', 'value': 'Un usuario malicioso local puede burlar el motor de detección de Falco a través de la versión 0.28.1 ejecutando un programa que altera los argumentos de las llamadas al sistema que se están ejecutando. El problema se ha solucionado en las versione

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2009-5151
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2009-5150
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2009-5152
200
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,absolute********
[{'cve': {'id': 'CVE-2018-16715', 'sourceIdentifier': 'cve@mitre.org', 'published': '2018-09-08T10:29:01.087', 'lastModified': '2019-10-03T00:03:26.223', 'vulnStatus': 'Analyzed', 'descriptions': [{'lang': 'en', 'value': 'An issue was discovered in Absolute Software CTES Windows Agent through 1.0.0.1479. The security permissions on the %ProgramData%\\CTES folder and sub-folders may allow write access to low-privileged user accounts. This allows unauthorized replacement of service program executable (EXE) or dynamically loadable library (DLL) files, causing elevated (SYSTEM) user access. Configuration control files or data files under this folder could also be similarly modified

cve_basic: 8
cve_metrics: 8
cve_weaknesses: 4
---- DONE absolute----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,uab********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE uab----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,baustem********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE baustem----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,vitelcom********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE vitelcom----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,valeo********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE valeo----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,worldelite********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE worldelite----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,cresyn********
[]
cve_basic: 0
cve_metrics: 0
cve_weakne

...

cve_basic: 165
cve_metrics: 160
cve_weaknesses: 91
---- DONE mitel----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,crescent********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE crescent----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,packard********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE packard----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,telsey********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE telsey----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,ddos-guard********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE ddos-guard----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,modnnet********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE modnnet----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,mita-teknik********
[]
cve_basic: 0
cve_metr

cve_basic: 37
cve_metrics: 34
cve_weaknesses: 19
---- DONE 3cx----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,excellent********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE excellent----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,tidomat********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE tidomat----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,contal********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE contal----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,primevolt********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE primevolt----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,clariphy********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE clariphy----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,convision********
[]
cve_basic: 0
cve_metrics:

cve_basic: 44
cve_metrics: 35
cve_weaknesses: 22
---- DONE vanderbilt----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-15956
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-3184
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-3185
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-3186
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2007-4582
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2007-4583
200
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,acti********
[{'cve': {'id': 'CVE-2020-15956', 'sourceIdentifier': 'cve@mitre.org', 'published': '2020-08-04T20:15:12.290', 'lastModified': '2020-08-06T19:38:53.273', 'vulnStatus': 'Analyzed', 'descriptions': [{'lang': 'en', 'value': 'ActiveMediaServer.exe in ACTi NVR3 Standard Server 3.0.12.42 allows remote unauthenticated attackers to trigger a buffer overflow and application termination via a malformed payl

cve_basic: 12
cve_metrics: 10
cve_weaknesses: 9
---- DONE acti----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2005-2127
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2007-4315
200
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,ati********
[{'cve': {'id': 'CVE-2005-2127', 'sourceIdentifier': 'secure@microsoft.com', 'published': '2005-08-19T04:00:00.000', 'lastModified': '2018-10-19T15:32:34.783', 'vulnStatus': 'Modified', 'descriptions': [{'lang': 'en', 'value': 'Microsoft Internet Explorer 5.01, 5.5, and 6 allows remote attackers to cause a denial of service (application crash) and possibly execute arbitrary code via a web page with embedded CLSIDs that reference certain COM objects that are not intended for use within Internet Explorer, as originally demonstrated using the (1) DDS Library Shape Control (Msdds.dll) COM object, and other objects including (2) Blnmgrps.dll, (3) Ciodm.dll, (4) Comsvcs.dll, (5) Danim.dll, (6) Html

cve_basic: 3
cve_metrics: 2
cve_weaknesses: 2
---- DONE ati----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,shinmaywa********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE shinmaywa----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,bluecom********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE bluecom----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2014-5704
200
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,dish********
[{'cve': {'id': 'CVE-2014-5704', 'sourceIdentifier': 'cret@cert.org', 'published': '2014-09-09T10:55:08.473', 'lastModified': '2016-06-17T02:00:14.770', 'vulnStatus': 'Analyzed', 'descriptions': [{'lang': 'en', 'value': 'The DISH Anywhere (aka com.sm.SlingGuide.Dish) application 3.5.10 for Android does not verify X.509 certificates from SSL servers, which allows man-in-the-middle attackers to spoof servers and obtain sensitive information via a c

In [40]:
collect_load_CVE(cveIDs_BT,"BT Vendors",url=URL)

UPLODING
----insert vulnerabilities into database----
******** BT Vendors,part********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE part----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-28047
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-28062
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-25542
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-28051
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-28046
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-25942
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-25941
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-25940
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-28069
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-5330
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3744
200
https://services.nvd.nist.gov/res

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-45100
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-45099
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3721
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34405
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-23691
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-5387
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-24423
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-45103
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2023-23690
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34457
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34436
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34435
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34399
200
https://services.nvd.nist.gov/rest/j

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34378
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34371
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34369
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-31232
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-33935
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34383
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34373
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-31233
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34379
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34372
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34380
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34368
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-34375
200
https://services.nvd.nist.gov/rest

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-26854
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3733
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3731
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3730
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3729
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3732
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-23155
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-23156
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-23158
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-23157
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3710
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2019-3728
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-24415
200
https://services.nvd.nist.gov/rest/json/c

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-8012
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-4997
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2017-8011
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2015-4056
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2015-4057
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-36281
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-36280
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-21599
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-21595
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-21594
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-21592
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-36279
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2021-21597
200
https://services.nvd.nist.gov/rest/json

...

cve_basic: 1
cve_metrics: 1
cve_weaknesses: 1
---- DONE diamond----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,e3control********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE e3control----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,qualica********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE qualica----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,anerma********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE anerma----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,qudelix********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE qudelix----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,ksh********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE ksh----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,amercom********
[]
cve_basic: 0
cve_metrics: 0
cve_weakness

cve_basic: 32
cve_metrics: 32
cve_weaknesses: 17
---- DONE sma----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,eurem********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE eurem----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,sz********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE sz----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,cordant********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE cordant----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,aja********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE aja----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,lineage********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE lineage----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,cetacean********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE 

cve_basic: 9
cve_metrics: 5
cve_weaknesses: 5
---- DONE sitecom----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,longconn********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE longconn----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,presence********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE presence----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,analog********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE analog----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,capinfo********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE capinfo----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,workstation********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE workstation----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,george********
[]
cve_basic: 0
cve_metrics:

200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-3216
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-36293
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2022-36381
200
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-13109
200
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,nintendo********
[{'cve': {'id': 'CVE-2022-47949', 'sourceIdentifier': 'cve@mitre.org', 'published': '2022-12-24T23:15:09.010', 'lastModified': '2023-01-06T20:17:13.450', 'vulnStatus': 'Analyzed', 'descriptions': [{'lang': 'en', 'value': 'The Nintendo NetworkBuffer class, as used in Animal Crossing: New Horizons before 2.0.6 and other products, allows remote attackers to execute arbitrary code via a large UDP packet that causes a buffer overflow, aka ENLBufferPwn. The victim must join a game session with the attacker. Other affected products include Mario Kart 7 before 1.2, Mario Kart 8, Mario Kart 8 Deluxe before 2.1.0

cve_basic: 9
cve_metrics: 9
cve_weaknesses: 5
---- DONE nintendo----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,mag-tek********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE mag-tek----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,meso********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE meso----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,ilshin********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE ilshin----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,stoneridge********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE stoneridge----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,global********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE global----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,qisda********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknes

In [6]:
collect_load_CVE(cveIDs_BT,"BT Vendors",url=URL)

UPLODING
----insert vulnerabilities into database----
******** BT Vendors,tonal********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE tonal----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,bioscrypt********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE bioscrypt----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,ketron********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE ketron----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,spectragraphics********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE spectragraphics----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,homa********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE homa----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,jetter********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE jetter----
UPLODING
----insert vulnerab

403
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,cc********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE cc----
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2020-36445
403
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,project********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE project----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,kasten********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE kasten----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,sle********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE sle----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,zhongshan********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE zhongshan----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,appro********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses

403
https://services.nvd.nist.gov/rest/json/cves/2.0?cveId=CVE-2015-7912
403
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,tibbo********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE tibbo----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,skullcandy********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE skullcandy----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,ineoquest********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE ineoquest----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,chromatek********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE chromatek----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,77********
[]
cve_basic: 0
cve_metrics: 0
cve_weaknesses: 0
---- DONE 77----
UPLODING
----insert vulnerabilities into database----
******** BT Vendors,copan********
[]
cve_basic: 0
cve_metrics: 0

In [ ]:
collect_load_CVE(cveIDs_BT,"BT Vendors",url=URL)

# Cipher of BT